# Segmenting and Clustering Neighbourhoods in Toronto
---
# Part 1
Import libraries

In [68]:
import pandas as pd
import numpy as np
import requests

Get the HTML page of Wikipedia and use read_html we convert the html data into list of Data frame objects.

Remove cells which have neighbourhood as "Not assigned."

In [69]:
wiki = 'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'
wiki_page = requests.get(wiki)

wiki_raw = pd.read_html(wiki_page.content, header = 0)[0]
df = wiki_raw[wiki_raw.Neighbourhood != 'Not assigned']
df.reset_index(inplace=True, drop=True)
df.head()

Postal Code           Borough                                Neighbourhood
0         M3A        North York                                    Parkwoods
1         M4A        North York                             Victoria Village
2         M5A  Downtown Toronto                    Regent Park, Harbourfront
3         M6A        North York             Lawrence Manor, Lawrence Heights
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [70]:
df.groupby(['Postal Code']).first()

Borough                                      Neighbourhood
Postal Code                                                                
M1B          Scarborough                                     Malvern, Rouge
M1C          Scarborough             Rouge Hill, Port Union, Highland Creek
M1E          Scarborough                  Guildwood, Morningside, West Hill
M1G          Scarborough                                             Woburn
M1H          Scarborough                                          Cedarbrae
...                  ...                                                ...
M9N                 York                                             Weston
M9P            Etobicoke                                          Westmount
M9R            Etobicoke  Kingsview Village, St. Phillips, Martin Grove ...
M9V            Etobicoke  South Steeles, Silverstone, Humbergate, Jamest...
M9W            Etobicoke                Northwest, West Humber - Clairville

[103 rows x 2 columns]

In [71]:
len(df['Postal Code'].unique())

103

In [72]:
df[df['Borough'] == 'Not assigned']

Empty DataFrame
Columns: [Postal Code, Borough, Neighbourhood]
Index: []

In [73]:
df.shape

(103, 3)

---
# Part 2

In [74]:
pip install geocoder

Note: you may need to restart the kernel to use updated packages.


In [75]:
import geocoder

In [76]:
url = 'http://cocl.us/Geospatial_data'
df_geo = pd.read_csv(url)
df_geo.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [77]:
df_geo.dtypes

Postal Code     object
Latitude       float64
Longitude      float64
dtype: object

In [78]:
df.dtypes

Postal Code      object
Borough          object
Neighbourhood    object
dtype: object

In [79]:
df.shape

(103, 3)

In [80]:
df_geo.shape

(103, 3)

In [81]:
df = df.join(df_geo.set_index('Postal Code'), on='Postal Code')
df.head(12)

Postal Code           Borough  \
0          M3A        North York   
1          M4A        North York   
2          M5A  Downtown Toronto   
3          M6A        North York   
4          M7A  Downtown Toronto   
5          M9A         Etobicoke   
6          M1B       Scarborough   
7          M3B        North York   
8          M4B         East York   
9          M5B  Downtown Toronto   
10         M6B        North York   
11         M9B         Etobicoke   

                                        Neighbourhood   Latitude  Longitude  
0                                           Parkwoods  43.753259 -79.329656  
1                                    Victoria Village  43.725882 -79.315572  
2                           Regent Park, Harbourfront  43.654260 -79.360636  
3                    Lawrence Manor, Lawrence Heights  43.718518 -79.464763  
4         Queen's Park, Ontario Provincial Government  43.662301 -79.389494  
5             Islington Avenue, Humber Valley Village  43.667856 -79.532242  
6                                      Malvern, Rouge  43.806686 -79.194353  
7                                           Don Mills  43.745906 -79.352188  
8                     Parkview Hill, Woodbine Gardens  43.706397 -79.309937  
9                            Garden District, Ryerson  43.657162 -79.378937  
10                                          Glencairn  43.709577 -79.445073  
11  West Deane Park, Princess Gardens, Martin Grov...  43.650943 -79.554724

In [82]:
df.shape

(103, 5)

---
# Part 3
Using the foursquere API to segment and cluster the neighborhoods of Toronto

In [85]:
!conda install -c conda-forge geocoder --yes
import geocoder
!pip install geopy
from geopy.geocoders import Nominatim 

address = 'Toronto, Ontario'

geolocator = Nominatim(user_agent="toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

Solving environment: ...working... done

# All requested packages already installed.

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


Printing the map

In [89]:
import folium

# create map of Toronto using latitude and longitude values
map_Toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(df['Latitude'], df['Longitude'], df['Borough'], df['Neighbourhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        ).add_to(map_Toronto)  
    
map_Toronto

Define Foursquare parameters

In [90]:
CLIENT_ID = 'MPMD3J0GGDV0HKDJFEDRK0USSGW0MQUD0DMN3C4ZAMWT2XTN'
CLIENT_SECRET = 'YVCSGVSCX02EFWITMI3RDOTUSJEHV4APRMLBFCN5CKWXCTPJ'

In [91]:
VERSION = '20180604' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: MPMD3J0GGDV0HKDJFEDRK0USSGW0MQUD0DMN3C4ZAMWT2XTN
CLIENT_SECRET:YVCSGVSCX02EFWITMI3RDOTUSJEHV4APRMLBFCN5CKWXCTPJ


Explore the data, and get the venues in 500 meters range from our first entry

In [93]:
neighborhood_latitude = df.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = df.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = df.loc[0, 'Neighbourhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Parkwoods are 43.7532586, -79.3296565.


Create the GET request URL

In [94]:
LIMIT = 100
radius = 500
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url

'https://api.foursquare.com/v2/venues/explore?&client_id=MPMD3J0GGDV0HKDJFEDRK0USSGW0MQUD0DMN3C4ZAMWT2XTN&client_secret=YVCSGVSCX02EFWITMI3RDOTUSJEHV4APRMLBFCN5CKWXCTPJ&v=20180604&ll=43.7532586,-79.3296565&radius=500&limit=100'

In [95]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5f1dab2fb0d9d01cac2a7fbc'},
 'response': {'warning': {'text': "There aren't a lot of results near you. Try something more general, reset your filters, or expand the search area."},
  'headerLocation': 'Parkwoods - Donalda',
  'headerFullLocation': 'Parkwoods - Donalda, Toronto',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 2,
  'suggestedBounds': {'ne': {'lat': 43.757758604500005,
    'lng': -79.32343823984928},
   'sw': {'lat': 43.7487585955, 'lng': -79.33587476015072}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4e8d9dcdd5fbbbb6b3003c7b',
       'name': 'Brookbanks Park',
       'location': {'address': 'Toronto',
        'lat': 43.751976046055574,
        'lng': -79.33214044722958,
        'labeledLatLngs': 

In [96]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [97]:
import json
from pandas.io.json import json_normalize

venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

C:\Users\my_user\anaconda3\lib\site-packages\ipykernel_launcher.py:6: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  


name         categories        lat        lng
0  Brookbanks Park               Park  43.751976 -79.332140
1    Variety Store  Food & Drink Shop  43.751974 -79.333114

Generalize to obtain the venues from all neighbourhoods in Toronto

In [98]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [100]:
toronto_venues = getNearbyVenues(names=df['Neighbourhood'],
                                   latitudes=df['Latitude'],
                                   longitudes=df['Longitude']
                                  )

Parkwoods
Victoria Village
Regent Park, Harbourfront
Lawrence Manor, Lawrence Heights
Queen's Park, Ontario Provincial Government
Islington Avenue, Humber Valley Village
Malvern, Rouge
Don Mills
Parkview Hill, Woodbine Gardens
Garden District, Ryerson
Glencairn
West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale
Rouge Hill, Port Union, Highland Creek
Don Mills
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate, Bloordale Gardens, Old Burnhamthorpe, Markland Wood
Guildwood, Morningside, West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
my_usertie
Cedarbrae
Hillcrest Village
Bathurst Manor, Wilson Heights, Downsview North
Thorncliffe Park
Richmond, Adelaide, King
Dufferin, Dovercourt Village
Scarborough Village
Fairview, Henry Farm, Oriole
Northwood Park, York University
East Toronto, Broadview North (Old East York)
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
Kennedy Park, Ionview, East Birch

Checking the size of df

In [101]:
print(toronto_venues.shape)
toronto_venues.head()

(2153, 7)


Neighbourhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2  Victoria Village              43.725882              -79.315572   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                    Venue  Venue Latitude  Venue Longitude  \
0         Brookbanks Park       43.751976       -79.332140   
1           Variety Store       43.751974       -79.333114   
2  Victoria Village Arena       43.723481       -79.315635   
3               Portugril       43.725819       -79.312785   
4             Tim Hortons       43.725517       -79.313103   

          Venue Category  
0                   Park  
1      Food & Drink Shop  
2           Hockey Arena  
3  Portuguese Restaurant  
4            Coffee Shop

Checking how many venues there are for each venue

In [102]:
toronto_venues.groupby('Neighbourhood').count()

Neighborhood Latitude  \
Neighbourhood                                                            
Agincourt                                                            4   
Alderwood, Long Branch                                               8   
Bathurst Manor, Wilson Heights, Downsview North                     21   
Bayview Village                                                      4   
Bedford Park, Lawrence Manor East                                   25   
...                                                                ...   
Willowdale, Willowdale East                                         34   
Willowdale, Willowdale West                                          6   
Woburn                                                               4   
Woodbine Heights                                                     9   
York Mills West                                                      3   

                                                 Neighborhood Longitude  \
Neighbourhood                                                             
Agincourt                                                             4   
Alderwood, Long Branch                                                8   
Bathurst Manor, Wilson Heights, Downsview North                      21   
Bayview Village                                                       4   
Bedford Park, Lawrence Manor East                                    25   
...                                                                 ...   
Willowdale, Willowdale East                                          34   
Willowdale, Willowdale West                                           6   
Woburn                                                                4   
Woodbine Heights                                                      9   
York Mills West                                                       3   

                                                 Venue  Venue Latitude  \
Neighbourhood                                                            
Agincourt                                            4               4   
Alderwood, Long Branch                               8               8   
Bathurst Manor, Wilson Heights, Downsview North     21              21   
Bayview Village                                      4               4   
Bedford Park, Lawrence Manor East                   25              25   
...                                                ...             ...   
Willowdale, Willowdale East                         34              34   
Willowdale, Willowdale West                          6               6   
Woburn                                               4               4   
Woodbine Heights                                     9               9   
York Mills West                                      3               3   

                                                 Venue Longitude  \
Neighbourhood                                                      
Agincourt                                                      4   
Alderwood, Long Branch                                         8   
Bathurst Manor, Wilson Heights, Downsview North               21   
Bayview Village                                                4   
Bedford Park, Lawrence Manor East                             25   
...                                                          ...   
Willowdale, Willowdale East                                   34   
Willowdale, Willowdale West                                    6   
Woburn                                                         4   
Woodbine Heights                                               9   
York Mills West                                                3   

                                                 Venue Category  
Neighbourhood                                                    
Agincourt                                                     4  
Alderwood, Long Branch                                        8 

How many categorys can we find?

In [103]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighbourhood'] = toronto_venues['Neighbourhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Neighbourhood  Accessories Store  Afghan Restaurant  Airport  \
0         Parkwoods                  0                  0        0   
1         Parkwoods                  0                  0        0   
2  Victoria Village                  0                  0        0   
3  Victoria Village                  0                  0        0   
4  Victoria Village                  0                  0        0   

   Airport Food Court  Airport Lounge  Airport Service  Airport Terminal  \
0                   0               0                0                 0   
1                   0               0                0                 0   
2                   0               0                0                 0   
3                   0               0                0                 0   
4                   0               0                0                 0   

   American Restaurant  Antique Shop  ...  Vegetarian / Vegan Restaurant  \
0                    0             0  ...                              0   
1                    0             0  ...                              0   
2                    0             0  ...                              0   
3                    0             0  ...                              0   
4                    0             0  ...                              0   

   Video Game Store  Video Store  Vietnamese Restaurant  Warehouse Store  \
0                 0            0                      0                0   
1                 0            0                      0                0   
2                 0            0                      0                0   
3                 0            0                      0                0   
4                 0            0                      0                0   

   Wine Bar  Wine Shop  Wings Joint  Women's Store  Yoga Studio  
0         0          0            0              0            0  
1         0          0            0              0            0  
2         0          0            0              0            0  
3         0          0            0              0            0  
4         0          0            0              0            0  

[5 rows x 270 columns]

In [104]:
toronto_onehot.shape

(2153, 270)

In [105]:
toronto_grouped = toronto_onehot.groupby('Neighbourhood').mean().reset_index()
toronto_grouped.head()

Neighbourhood  Accessories Store  \
0                                        Agincourt                0.0   
1                           Alderwood, Long Branch                0.0   
2  Bathurst Manor, Wilson Heights, Downsview North                0.0   
3                                  Bayview Village                0.0   
4                Bedford Park, Lawrence Manor East                0.0   

   Afghan Restaurant  Airport  Airport Food Court  Airport Lounge  \
0                0.0      0.0                 0.0             0.0   
1                0.0      0.0                 0.0             0.0   
2                0.0      0.0                 0.0             0.0   
3                0.0      0.0                 0.0             0.0   
4                0.0      0.0                 0.0             0.0   

   Airport Service  Airport Terminal  American Restaurant  Antique Shop  ...  \
0              0.0               0.0                 0.00           0.0  ...   
1              0.0               0.0                 0.00           0.0  ...   
2              0.0               0.0                 0.00           0.0  ...   
3              0.0               0.0                 0.00           0.0  ...   
4              0.0               0.0                 0.04           0.0  ...   

   Vegetarian / Vegan Restaurant  Video Game Store  Video Store  \
0                            0.0               0.0          0.0   
1                            0.0               0.0          0.0   
2                            0.0               0.0          0.0   
3                            0.0               0.0          0.0   
4                            0.0               0.0          0.0   

   Vietnamese Restaurant  Warehouse Store  Wine Bar  Wine Shop  Wings Joint  \
0                    0.0              0.0       0.0        0.0          0.0   
1                    0.0              0.0       0.0        0.0          0.0   
2                    0.0              0.0       0.0        0.0          0.0   
3                    0.0              0.0       0.0        0.0          0.0   
4                    0.0              0.0       0.0        0.0          0.0   

   Women's Store  Yoga Studio  
0           0.00          0.0  
1           0.00          0.0  
2           0.00          0.0  
3           0.00          0.0  
4           0.04          0.0  

[5 rows x 270 columns]

In [106]:
toronto_grouped.shape

(96, 270)

Getting the top 10 for each neighbourhood

In [107]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [108]:
import numpy as np
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighbourhood'] = toronto_grouped['Neighbourhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighbourhood 1st Most Common Venue  \
0                                        Agincourt                Lounge   
1                           Alderwood, Long Branch           Pizza Place   
2  Bathurst Manor, Wilson Heights, Downsview North           Coffee Shop   
3                                  Bayview Village                  Café   
4                Bedford Park, Lawrence Manor East        Sandwich Place   

       2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0  Latin American Restaurant          Skating Rink        Breakfast Spot   
1                   Pharmacy        Sandwich Place          Dance Studio   
2                       Bank    Frozen Yogurt Shop           Bridal Shop   
3                       Bank    Chinese Restaurant   Japanese Restaurant   
4                 Restaurant    Italian Restaurant           Coffee Shop   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0            Donut Shop                 Diner        Discount Store   
1           Coffee Shop                   Pub                   Gym   
2        Sandwich Place                 Diner            Restaurant   
3           Yoga Studio                 Diner        Discount Store   
4          Liquor Store       Thai Restaurant                  Café   

  8th Most Common Venue      9th Most Common Venue 10th Most Common Venue  
0   Distribution Center                    Dog Run       Doner Restaurant  
1      Airport Terminal         Falafel Restaurant            Event Space  
2         Deli / Bodega  Middle Eastern Restaurant            Supermarket  
3   Distribution Center                    Dog Run       Doner Restaurant  
4                   Pub                    Butcher       Sushi Restaurant

Clustering Neighborhoods

In [109]:
# import k-means from clustering stage
from sklearn.cluster import KMeans

# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighbourhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1])

Merge the dataframe with the top 10 and the cluster for each neighbourhood

In [121]:
df

Postal Code           Borough  \
0           M3A        North York   
1           M4A        North York   
2           M5A  Downtown Toronto   
3           M6A        North York   
4           M7A  Downtown Toronto   
..          ...               ...   
98          M8X         Etobicoke   
99          M4Y  Downtown Toronto   
100         M7Y      East Toronto   
101         M8Y         Etobicoke   
102         M8Z         Etobicoke   

                                         Neighbourhood   Latitude  Longitude  
0                                            Parkwoods  43.753259 -79.329656  
1                                     Victoria Village  43.725882 -79.315572  
2                            Regent Park, Harbourfront  43.654260 -79.360636  
3                     Lawrence Manor, Lawrence Heights  43.718518 -79.464763  
4          Queen's Park, Ontario Provincial Government  43.662301 -79.389494  
..                                                 ...        ...        ...  
98       The Kingsway, Montgomery Road, Old Mill North  43.653654 -79.506944  
99                                Church and Wellesley  43.665860 -79.383160  
100  Business reply mail Processing Centre, South C...  43.662744 -79.321558  
101  Old Mill South, King's Mill Park, Sunnylea, Hu...  43.636258 -79.498509  
102  Mimico NW, The Queensway West, South of Bloor,...  43.628841 -79.520999  

[103 rows x 5 columns]

In [113]:
toronto_merged[toronto_merged['Cluster Labels'].isnull()]

Postal Code      Borough                            Neighbourhood  \
5          M9A    Etobicoke  Islington Avenue, Humber Valley Village   
45         M2L   North York                 York Mills, Silver Hills   
95         M1X  Scarborough                              Upper Rouge   

     Latitude  Longitude  Cluster Labels 1st Most Common Venue  \
5   43.667856 -79.532242             NaN                   NaN   
45  43.757490 -79.374714             NaN                   NaN   
95  43.836125 -79.205636             NaN                   NaN   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
5                    NaN                   NaN                   NaN   
45                   NaN                   NaN                   NaN   
95                   NaN                   NaN                   NaN   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
5                    NaN                   NaN                   NaN   
45                   NaN                   NaN                   NaN   
95                   NaN                   NaN                   NaN   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
5                    NaN                   NaN                    NaN  
45                   NaN                   NaN                    NaN  
95                   NaN                   NaN                    NaN

Plot the clusters in the map

In [115]:
import matplotlib.cm as cm
import matplotlib.colors as colors

# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

toronto_merged_nonan = toronto_merged.dropna(subset=['Cluster Labels'])

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged_nonan['Latitude'], toronto_merged_nonan['Longitude'], toronto_merged_nonan['Neighbourhood'], toronto_merged_nonan['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster-1)],
        fill=True,
        fill_color=rainbow[int(cluster-1)],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

Cluster 1

In [116]:
toronto_merged_nonan.loc[toronto_merged_nonan['Cluster Labels'] == 0, toronto_merged_nonan.columns[[1] + list(range(5, toronto_merged_nonan.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
0         North York             0.0                  Park   
21              York             0.0                  Park   
35         East York             0.0                  Park   
52        North York             0.0                  Park   
64              York             0.0                  Park   
66        North York             0.0                  Park   
85       Scarborough             0.0                  Park   
91  Downtown Toronto             0.0                  Park   

         2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0            Food & Drink Shop           Yoga Studio            Donut Shop   
21               Women's Store                  Pool           Yoga Studio   
35           Convenience Store           Yoga Studio            Donut Shop   
52                 Yoga Studio            Donut Shop    Dim Sum Restaurant   
64           Convenience Store           Yoga Studio            Donut Shop   
66  Construction & Landscaping     Convenience Store           Yoga Studio   
85                  Playground           Coffee Shop           Yoga Studio   
91                       Trail            Playground           Yoga Studio   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0                  Diner        Discount Store   Distribution Center   
21      Doner Restaurant    Dim Sum Restaurant                 Diner   
35                 Diner        Discount Store   Distribution Center   
52                 Diner        Discount Store   Distribution Center   
64                 Diner        Discount Store   Distribution Center   
66            Donut Shop                 Diner        Discount Store   
85      Doner Restaurant    Dim Sum Restaurant                 Diner   
91          Dessert Shop    Dim Sum Restaurant                 Diner   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0                Dog Run      Doner Restaurant              Drugstore  
21        Discount Store   Distribution Center                Dog Run  
35               Dog Run      Doner Restaurant    Dumpling Restaurant  
52               Dog Run      Doner Restaurant              Drugstore  
64               Dog Run      Doner Restaurant    Dumpling Restaurant  
66   Distribution Center               Dog Run       Doner Restaurant  
85        Discount Store   Distribution Center                Dog Run  
91        Discount Store   Distribution Center                Dog Run

Cluster 2

In [117]:
toronto_merged_nonan.loc[toronto_merged_nonan['Cluster Labels'] == 1, toronto_merged_nonan.columns[[1] + list(range(5, toronto_merged_nonan.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
1          North York             1.0          Hockey Arena   
2    Downtown Toronto             1.0           Coffee Shop   
3          North York             1.0        Clothing Store   
4    Downtown Toronto             1.0           Coffee Shop   
6         Scarborough             1.0            Print Shop   
..                ...             ...                   ...   
97   Downtown Toronto             1.0           Coffee Shop   
98          Etobicoke             1.0                 River   
99   Downtown Toronto             1.0           Coffee Shop   
100      East Toronto             1.0    Light Rail Station   
102         Etobicoke             1.0         Grocery Store   

    2nd Most Common Venue 3rd Most Common Venue  4th Most Common Venue  \
1             Pizza Place           Coffee Shop  Portuguese Restaurant   
2                  Bakery                   Pub                   Park   
3       Accessories Store           Coffee Shop               Boutique   
4                   Diner           Yoga Studio                    Bar   
6    Fast Food Restaurant           Yoga Studio     Dim Sum Restaurant   
..                    ...                   ...                    ...   
97                   Café                 Hotel             Restaurant   
98       Doner Restaurant          Dessert Shop     Dim Sum Restaurant   
99       Sushi Restaurant   Japanese Restaurant                Gay Bar   
100           Yoga Studio         Auto Workshop             Smoke Shop   
102         Tanning Salon     Convenience Store         Discount Store   

    5th Most Common Venue 6th Most Common Venue   7th Most Common Venue  \
1             Yoga Studio    Dim Sum Restaurant                   Diner   
2          Breakfast Spot                  Café                 Theater   
3      Miscellaneous Shop           Event Space  Furniture / Home Store   
4                Beer Bar         Smoothie Shop          Sandwich Place   
6                   Diner        Discount Store     Distribution Center   
..                    ...                   ...                     ...   
97                    Gym   Japanese Restaurant     American Restaurant   
98                  Diner        Discount Store     Distribution Center   
99             Restaurant           Yoga Studio         Bubble Tea Shop   
100               Brewery                   Spa          Farmers Market   
102         Burrito Place          Burger Joint          Sandwich Place   

    8th Most Common Venue     9th Most Common Venue 10th Most Common Venue  
1          Discount Store       Distribution Center                Dog Run  
2             Yoga Studio        Mexican Restaurant             Shoe Store  
3           Women's Store     Vietnamese Restaurant      Convenience Store  
4           Burrito Place                      Café                   Park  
6                 Dog Run          Doner Restaurant             Donut Shop  
..                    ...                       ...                    ...  
97             Steakhouse          Asian Restaurant     Seafood Restaurant  
98                Dog Run               Yoga Studio       Department Store  
99           Dance Studio  Mediterranean Restaurant            Men's Store  
100  Fast Food Restaurant             Burrito Place             Restaurant  
102            Kids Store           Supplement Shop                 Bakery  

[87 rows x 12 columns]

Cluster 3

In [118]:
toronto_merged_nonan.loc[toronto_merged_nonan['Cluster Labels'] == 2, toronto_merged_nonan.columns[[1] + list(range(5, toronto_merged_nonan.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
32  Scarborough             2.0           Pizza Place            Playground   
50   North York             2.0           Pizza Place      Department Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
32      Doner Restaurant          Dessert Shop    Dim Sum Restaurant   
50           Event Space  Ethiopian Restaurant     Electronics Store   

          6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
32                        Diner        Discount Store   Distribution Center   
50  Eastern European Restaurant   Dumpling Restaurant             Drugstore   

   9th Most Common Venue 10th Most Common Venue  
32               Dog Run             Donut Shop  
50            Donut Shop       Doner Restaurant

Cluster 4

In [119]:
toronto_merged_nonan.loc[toronto_merged_nonan['Cluster Labels'] == 3, toronto_merged_nonan.columns[[1] + list(range(5, toronto_merged_nonan.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
57   North York             3.0           Fabric Shop        Baseball Field   
101   Etobicoke             3.0        Baseball Field           Yoga Studio   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
57            Yoga Studio            Donut Shop                 Diner   
101            Donut Shop                 Diner        Discount Store   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
57         Discount Store   Distribution Center               Dog Run   
101   Distribution Center               Dog Run      Doner Restaurant   

    9th Most Common Venue 10th Most Common Venue  
57       Doner Restaurant              Drugstore  
101             Drugstore         Farmers Market

Cluster 5

In [120]:
toronto_merged_nonan.loc[toronto_merged_nonan['Cluster Labels'] == 4, toronto_merged_nonan.columns[[1] + list(range(5, toronto_merged_nonan.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
11  Etobicoke             4.0         Jewelry Store           Yoga Studio   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
11                 Diner        Discount Store   Distribution Center   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
11               Dog Run      Doner Restaurant            Donut Shop   

   9th Most Common Venue 10th Most Common Venue  
11             Drugstore         Farmers Market